# TP Programmation avec Keras - Density Neural Network

Nous allons mettre en place un Density Neural Network afin d'effectuer une prédiction d'incertitudes.

Dans ce TP, des cellules seront laissées à trous, il faudra les compléter suivant les consignes. Elles seront identifiées par le mot **Exercice**. Les **Vérifications** seront effectuées principalement par vous-mêmes, sur la bonne convergence des algorithmes ou leur bon fonctionnement.

Ci-dessous, on importe les bibliothèques qui seront utiles.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow.keras as keras
import tensorflow as tf

## Mise en place des données

Afin de pouvoir visualiser simplement, nous allons utiliser des données en une dimension (entrée et sortie) : un cosinus bruité avec un bruit gaussien. Ci-dessous, nous mettons en place les données.

In [ ]:
#NE PAS MODIFIER
N_train = 1000

X_train = np.random.rand(N_train)*8 - 4

sigma = np.abs(np.cos(X_train))*0.2

Y_train = np.cos(X_train) + np.random.normal(0, sigma)

N_test = 1000

X_test = np.linspace(-8,8,N_test)

Y_test = np.cos(X_test)

**Exercice** : Visualisez les données d'entraînement avec un scatter plot.

In [ ]:
#A COMPLETER

## Création d'une couche de densité et d'une loss function associée

Nous allons supposer que la sortie suite une loi de probabilité $p(y|x)$ normale de moyenne $\mu$ et d'écart-type $\sigma$. Nous allons chercher à prédire ces paramètres $\mu$ et $\sigma$. Pour ce faire, nous allons créer un type de couche adapté à leur prédiction.

Ci-dessous, nous créons une couche DenseNormal qui prend entrée un nombre $N$ de neurones et produit $2N$ sorties : chaque dimension produit un $\mu$ et un $\sigma$.

**Exerice** : $\sigma$ doit être strictement positif. Pour ce faire, appliquez la fonction tf.nn.softplus à logsigma. Ajoutez en plus un petit $\varepsilon$ pour éviter des divergences lors de l'apprentissage (éviter que $\sigma$ ne s'approche trop de 0. 1e-6 devrait suffire.

In [ ]:
class DenseNormal(keras.layers.Layer):
    def __init__(self, units):
        super(DenseNormal, self).__init__()
        self.units = int(units)
        self.dense = keras.layers.Dense(2 * self.units)

    def call(self, x):
        output = self.dense(x)
        mu, logsigma = tf.split(output, 2, axis=-1)
        sigma = #A COMPLETER AVEC tf.nn.softplus et l'ajout d'un epsilon
        return tf.concat([mu, sigma], axis=-1)

    def compute_output_shape(self, input_shape):
        return (input_shape[0], 2 * self.units)

    def get_config(self):
        base_config = super(DenseNormal, self).get_config()
        base_config['units'] = self.units
        return base_config

Nous allons créer ensuite la loss-function adaptée. Nous rappelons la vraisemblance de la loi gaussienne :

\begin{equation}
p(y|\mu,\theta) = \frac{1}{\sqrt{2\pi}\sigma} e^{-\frac{(y-\mu)^2}{2\sigma^2}}
\end{equation}

La log-vraisemblance associée est donc donnée par :

\begin{equation}
\log(p(y|\mu,\theta)) = -\log(\sqrt{2\pi}\sigma) - (\frac{(y-\mu)^2}{2\sigma^2})
\end{equation}

**Exercice** : Complétez le code suivant en indiquant l'ensemble de la log-vraisemblance.


In [ ]:
def Gaussian_NLL(y, net_output, reduce=True):
    mu, sigma = tf.split(net_output, 2, axis=-1)
    ax = list(range(1, len(y.shape)))

    logprob = #A COMPLETER
    loss = tf.reduce_mean(-logprob, axis=ax)
    return tf.reduce_mean(loss) if reduce else loss

## Modèle Keras

### Création du modèle

**Exercice** : Créez un modèle avec Keras que vous appellerez "my_model", uniquement fully_connected. La dernière couche sera une couche DenseNormal que vous avez créée, avec un seul neurone puisqu'on prédit une sortie à 1 dimension.

In [ ]:
#A COMPLETER

**Exercice** : Affichez la structure de votre modèle avec my_model.summary()

In [ ]:
#A COMPLETER

**Vérification** : Pour l'instant, il suffit qu'il n'y ait pas d'erreur.

### Compilation du modèle

**Exercice** : Il faut maintenant compiler le modèle en utilisant la fonction de coût que vous avez définie au-dessus avec la negative log-likelihood de la distribution gaussienne. Il suffit d'entrer le nom de la fonction en loss (sans guillemets). Il ne sera pas utile de mettre de métrique.

In [ ]:
#A COMPLETER

**Vérification** : De nouveau, s'il n'y a pas d'erreur et que vous avez suivi les instructions, tout devrait bien se passer.

## L'apprentissage

**Exercice** : Effectuez classiquement l'apprentissage.

In [ ]:
learning = #A COMPLETER

**Vérification** : La loss function devrait diminuer.

**Exercice** : Tracez l'évolution de la fonction de coût.

In [ ]:
loss_evolution = learning.history["loss"]


plt.figure(figsize = (16,9))
plt.plot(loss_evolution,label = "Train set")
plt.xlabel("Epoques")
plt.ylabel("Valeur de la fonction de coût")
plt.legend()
plt.title("Loss function evolution")


## Prédictions avec le modèle

**Exercice** : Effectuez une prédiction à partir de X_test.

In [ ]:
Y_pred_test = #A COMPLETER

**Exercice** : Séparez la prédiction en deux vecteurs mu et sigma.

In [ ]:
mu = #A COMPLETER
sigma = #A COMPLETER

Ci-dessous, voici la visualisation sur le jeu de test de votre prédiction (moyenne) et de l'incertitude associée. Les zones colorées correspondent aux incertitudes à 1, 2, 3 et 4 sigma.

In [ ]:
var = np.minimum(sigma, 1e3)
    
plt.figure(figsize=(5, 3), dpi=200)
plt.title("Aleatoric uncertainty")
plt.scatter(X_train, Y_train, s=1., c='#463c3c', zorder=0, label="Train")
plt.plot(X_test, Y_test, 'r--', zorder=2, label="True")
plt.plot(X_test, mu, color='#007cab', zorder=3, label="Pred")
plt.plot([-4, -4], [-150, 150], 'k--', alpha=0.4, zorder=0)
plt.plot([+4, +4], [-150, 150], 'k--', alpha=0.4, zorder=0)
for k in np.linspace(0, 4, 4):
    plt.fill_between(
        X_test, (mu - k * var), (mu + k * var),
        alpha=0.3,
        edgecolor=None,
        facecolor='#00aeef',
        linewidth=0,
        zorder=1,
        label="Unc." if k == 0 else None)
plt.gca().set_ylim(-2, 2)
plt.gca().set_xlim(-7, 7)
plt.legend(loc="upper left")